# Week 5 Thursday

In [1]:
import numpy as np
import pandas as pd
import altair as alt

Here is an elegant way to let pandas know how the missing values are represented in our dataset.  This is much more efficient than using `applymap` and a lambda function.

In [2]:
df = pd.read_csv("spotify_dataset.csv", na_values=" ")

Notice how the data types are correct (we didn't need to use `pd.to_numeric`).

In [3]:
df.dtypes

Index                          int64
Highest Charting Position      int64
Number of Times Charted        int64
Week of Highest Charting      object
Song Name                     object
Streams                       object
Artist                        object
Artist Followers             float64
Song ID                       object
Genre                         object
Release Date                  object
Weeks Charted                 object
Popularity                   float64
Danceability                 float64
Energy                       float64
Loudness                     float64
Speechiness                  float64
Acousticness                 float64
Liveness                     float64
Tempo                        float64
Duration (ms)                float64
Valence                      float64
Chord                         object
dtype: object

* Plot Acousticness vs Energy.

In [4]:
alt.Chart(df).mark_circle().encode(
    x = "Acousticness",
    y = "Energy"
)

alt.Chart(...)

If we fit a linear model to this data (with "Acousticness" as our only predictor and with "Energy" as our target), would you expect the coefficient to be positive or negative?  (You can either use the graph or intuition.  "Acousticness" is as opposed to for example electric guitars.)

* Check your answer using the `LinearRegression` from scikit-learn.

In [5]:
from sklearn.linear_model import LinearRegression

In [6]:
reg = LinearRegression()

The following is a very common error.  The problem is that `df["Acousticness"]` is one-dimensional, and scikit-learn wants something two-dimensional.  (It's fine and maybe required for the second input, `df["Energy"]`, to be one-dimensional.)

In [8]:
reg.fit(df["Acousticness"], df["Energy"])

ValueError: Expected 2D array, got 1D array instead:
array=[0.127  0.0383 0.335  ... 0.184  0.249  0.433 ].
Reshape your data either using array.reshape(-1, 1) if your data has a single feature or array.reshape(1, -1) if it contains a single sample.

In [9]:
df["Acousticness"]

0       0.12700
1       0.03830
2       0.33500
3       0.04690
4       0.02030
         ...   
1551    0.00261
1552    0.24000
1553    0.18400
1554    0.24900
1555    0.43300
Name: Acousticness, Length: 1556, dtype: float64

In [10]:
df[["Acousticness"]]

Acousticness
0          0.12700
1          0.03830
2          0.33500
3          0.04690
4          0.02030
...            ...
1551       0.00261
1552       0.24000
1553       0.18400
1554       0.24900
1555       0.43300

[1556 rows x 1 columns]

In [11]:
type(df["Acousticness"])

pandas.core.series.Series

In [12]:
type(df[["Acousticness"]])

pandas.core.frame.DataFrame

In [14]:
df[["Acousticness","Song Name","Artist"]]

Acousticness                           Song Name  \
0          0.12700                             Beggin'   
1          0.03830           STAY (with Justin Bieber)   
2          0.33500                            good 4 u   
3          0.04690                          Bad Habits   
4          0.02030   INDUSTRY BABY (feat. Jack Harlow)   
...            ...                                 ...   
1551       0.00261                           New Rules   
1552       0.24000                  Cheirosa - Ao Vivo   
1553       0.18400           Havana (feat. Young Thug)   
1554       0.24900          Surtada - Remix Brega Funk   
1555       0.43300  Lover (Remix) [feat. Shawn Mendes]   

                             Artist  
0                          Måneskin  
1                     The Kid LAROI  
2                    Olivia Rodrigo  
3                        Ed Sheeran  
4                         Lil Nas X  
...                             ...  
1551                       Dua Lipa  
1552                 Jorge & Mateus  
1553                 Camila Cabello  
1554  Dadá Boladão, Tati Zaqui, OIK  
1555                   Taylor Swift  

[1556 rows x 3 columns]

Another common error, not removing missing values.

In [15]:
reg.fit(df[["Acousticness"]], df["Energy"])

ValueError: Input X contains NaN.
LinearRegression does not accept missing values encoded as NaN natively. For supervised learning, you might want to consider sklearn.ensemble.HistGradientBoostingClassifier and Regressor which accept missing values encoded as NaNs natively. Alternatively, it is possible to preprocess the data, for instance by using an imputer transformer in a pipeline or drop samples with missing values. See https://scikit-learn.org/stable/modules/impute.html You can find a list of all estimators that handle NaN values at the following page: https://scikit-learn.org/stable/modules/impute.html#estimators-that-handle-nan-values

In [16]:
df_clean = df.dropna(axis = 0)

In [17]:
df.shape

(1556, 23)

In [18]:
df_clean.shape

(1545, 23)

In [19]:
reg.fit(df_clean[["Acousticness"]], df_clean["Energy"])

LinearRegression()

In [20]:
reg.coef_

array([-0.35010056])

In [21]:
reg.intercept_

0.7205632317364904

Look at the scatter plot above.  This coefficient and this intercept should look very reasonable.

What are the predicted outputs?

In [22]:
reg.predict(df_clean[["Acousticness"]])

array([0.67610046, 0.70715438, 0.60327954, ..., 0.65614473, 0.63338819,
       0.56896969])

Add a new column named "pred" with these predicted values.  A warning (not an error) will show up because we didn't use `copy()` above when dropping the rows with missing values.

In [23]:
df_clean["pred"] = reg.predict(df_clean[["Acousticness"]])

/tmp/ipykernel_74/632255384.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_clean["pred"] = reg.predict(df_clean[["Acousticness"]])


In [24]:
df_clean2 = df.dropna(axis = 0).copy()

In [25]:
df_clean2["pred"] = reg.predict(df_clean2[["Acousticness"]])

In [26]:
df_clean

Index  Highest Charting Position  Number of Times Charted  \
0         1                          1                        8   
1         2                          2                        3   
2         3                          1                       11   
3         4                          3                        5   
4         5                          5                        1   
...     ...                        ...                      ...   
1551   1552                        195                        1   
1552   1553                        196                        1   
1553   1554                        197                        1   
1554   1555                        198                        1   
1555   1556                        199                        1   

     Week of Highest Charting                           Song Name     Streams  \
0      2021-07-23--2021-07-30                             Beggin'  48,633,449   
1      2021-07-23--2021-07-30           STAY (with Justin Bieber)  47,248,719   
2      2021-06-25--2021-07-02                            good 4 u  40,162,559   
3      2021-07-02--2021-07-09                          Bad Habits  37,799,456   
4      2021-07-23--2021-07-30   INDUSTRY BABY (feat. Jack Harlow)  33,948,454   
...                       ...                                 ...         ...   
1551   2019-12-27--2020-01-03                           New Rules   4,630,675   
1552   2019-12-27--2020-01-03                  Cheirosa - Ao Vivo   4,623,030   
1553   2019-12-27--2020-01-03           Havana (feat. Young Thug)   4,620,876   
1554   2019-12-27--2020-01-03          Surtada - Remix Brega Funk   4,607,385   
1555   2019-12-27--2020-01-03  Lover (Remix) [feat. Shawn Mendes]   4,595,450   

                             Artist  Artist Followers                 Song ID  \
0                          Måneskin         3377762.0  3Wrjm47oTz2sjIgck11l5e   
1                     The Kid LAROI         2230022.0  5HCyWlXZPP0y6Gqq8TgA20   
2                    Olivia Rodrigo         6266514.0  4ZtFanR9U6ndgddUvNcjcG   
3                        Ed Sheeran        83293380.0  6PQ88X9TkUIAUIZJHW2upE   
4                         Lil Nas X         5473565.0  27NovPIUIRrOZoCHxABJwK   
...                             ...               ...                     ...   
1551                       Dua Lipa        27167675.0  2ekn2ttSfGqwhhate0LSR0   
1552                 Jorge & Mateus        15019109.0  2PWjKmjyTZeDpmOUa3a5da   
1553                 Camila Cabello        22698747.0  1rfofaqEpACxVEHIZBJe6W   
1554  Dadá Boladão, Tati Zaqui, OIK          208630.0  5F8ffc8KWKNawllr5WsW0r   
1555                   Taylor Swift        42227614.0  3i9UVldZOE0aD0JnyfAZZ0   

                                                  Genre  ... Energy Loudness  \
0                ['indie rock italiano', 'italian pop']  ...  0.800   -4.808   
1                                ['australian hip hop']  ...  0.764   -5.484   
2                                               ['pop']  ...  0.664   -5.044   
3                                     ['pop', 'uk pop']  ...  0.897   -3.712   
4                         ['lgbtq+ hip hop', 'pop rap']  ...  0.704   -7.409   
...                                                 ...  ...    ...      ...   
1551                     ['dance pop', 'pop', 'uk pop']  ...  0.700   -6.021   
1552           ['sertanejo', 'sertanejo universitario']  ...  0.870   -3.123   
1553  ['dance pop', 'electropop', 'pop', 'post-teen ...  ...  0.523   -4.333   
1554                     ['brega funk', 'funk carioca']  ...  0.550   -7.026   
1555                           ['pop', 'post-teen pop']  ...  0.603   -7.176   

      Speechiness  Acousticness  Liveness    Tempo  Duration (ms)  Valence  \
0          0.0504       0.12700    0.3590  134.002       211560.0    0.589   
1          0.0483       0.03830    0.1030  169.928       141806.0    0.478   
2          0.1540       0.33500    0.0849  166.928       178

Plot the fit values using a red `mark_line` in Altair.  Layer the two charts on top of each other.

In [30]:
c1 = alt.Chart(df_clean).mark_circle().encode(
    x = "Acousticness",
    y = "Energy"
)

In [31]:
c2 = alt.Chart(df_clean).mark_line(color="red").encode(
    x = "Acousticness",
    y = "pred"
)

In [32]:
c1+c2

alt.LayerChart(...)

Linear regression works basically the same with multiple input variables.  Perform linear regression using "Acousticness", "Speechiness", "Valence" as our input features.

In [33]:
reg2 = LinearRegression()

In [34]:
df_clean[["Acousticness", "Speechiness", "Valence"]]

Acousticness  Speechiness  Valence
0          0.12700       0.0504    0.589
1          0.03830       0.0483    0.478
2          0.33500       0.1540    0.688
3          0.04690       0.0348    0.591
4          0.02030       0.0615    0.894
...            ...          ...      ...
1551       0.00261       0.0694    0.608
1552       0.24000       0.0851    0.714
1553       0.18400       0.0300    0.394
1554       0.24900       0.0587    0.881
1555       0.43300       0.0640    0.422

[1545 rows x 3 columns]

In [35]:
reg2.fit(df_clean[["Acousticness", "Speechiness", "Valence"]],df_clean["Energy"])

LinearRegression()

In [36]:
reg2.coef_

array([-0.33557117, -0.08205736,  0.21893852])

Linear regression is not the fanciest machine learning model, but it is probably the most interpretable model.  For example, the coefficients above suggest that Acousticness generally corresponds to having less energy, Valence corresponds to more energy.

In [37]:
df_clean.corr()

Index  Highest Charting Position  \
Index                      1.000000                   0.251112   
Highest Charting Position  0.251112                   1.000000   
Number of Times Charted   -0.360013                  -0.417748   
Artist Followers           0.090887                  -0.233723   
Popularity                -0.333683                  -0.164167   
Danceability               0.126254                   0.017149   
Energy                    -0.018813                   0.063026   
Loudness                  -0.014321                   0.032166   
Speechiness                0.109213                   0.041248   
Acousticness              -0.063914                  -0.012924   
Liveness                   0.028976                   0.012718   
Tempo                      0.023622                   0.026235   
Duration (ms)             -0.023481                  -0.033956   
Valence                   -0.054632                   0.045362   
pred                       0.063914                   0.012924   

                           Number of Times Charted  Artist Followers  \
Index                                    -0.360013          0.090887   
Highest Charting Position                -0.417748         -0.233723   
Number of Times Charted                   1.000000          0.027458   
Artist Followers                          0.027458          1.000000   
Popularity                                0.232796          0.104358   
Danceability                              0.027026         -0.097576   
Energy                                   -0.061139         -0.065613   
Loudness                                  0.031225         -0.033264   
Speechiness                              -0.060216         -0.072968   
Acousticness                              0.046651          0.023830   
Liveness                                 -0.058436         -0.012491   
Tempo                                    -0.048307         -0.019881   
Duration (ms)                             0.033980          0.142145   
Valence                                   0.021570         -0.108804   
pred                                     -0.046651         -0.023830   

                           Popularity  Danceability    Energy  Loudness  \
Index                       -0.333683      0.126254 -0.018813 -0.014321   
Highest Charting Position   -0.164167      0.017149  0.063026  0.032166   
Number of Times Charted      0.232796      0.027026 -0.061139  0.031225   
Artist Followers             0.104358     -0.097576 -0.065613 -0.033264   
Popularity                   1.000000      0.028435  0.094691  0.158767   
Danceability                 0.028435      1.000000  0.142130  0.234928   
Energy                       0.094691      0.142130  1.000000  0.732616   
Loudness                     0.158767      0.234928  0.732616  1.000000   
Speechiness                 -0.032091      0.237394  0.023989 -0.018823   
Acousticness                -0.091245     -0.316798 -0.542399 -0.477431   
Liveness                    -0.029460     -0.114518  0.124693  0.043141   
Tempo                       -0.024951     -0.040219  0.113352  0.104371   
Duration (ms)                0.082096     -0.101390  0.056624  0.075262   
Valence                     -0.000953      0.361627  0.356325  0.298762   
pred                         0.091245      0.316798  0.542399  0.477431   

                           Speechiness  Acousticness  Liveness     Tempo  \
Index                         0.109213     -0.063914  0.028976  0.023622   
Highest Charting Position     0.041248     -0.012924  0.012718  0.026235   
Number of Times Charted      -0.060216      0.046651 -0.058436 -0.048307   
Artist Followers             -0.072968      0.023830 -0.012491 -0.019881   
Popularity                   -0.032091     -0.091245 -0.029460 -0.024951   
Danceability                  0.237394     -0.316798 -0.114518 -0.040219   
Energy                        0.023989     -0.542399  0.124693  0.113352   
Loudness   

reference: 

reference:
https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.copy.html
https://docs.python.org/3/library/copy.html
https://realpython.com/copying-python-objects/